In [108]:
##creating a trend based strategy on rsi 
##rsi crossing above 20,50,70 entry points rsi crossing below 80,50,20 selling points

In [109]:
##then when built this add sizing too ,how we have to figure it

In [331]:
import pandas as pd
import vectorbt as vbt
import ta
import numpy as np

data = pd.read_csv('btc_1h_test.csv')   
column_names = ['datetime', 'open', 'high', 'low', 'close', 'volume']
data.columns = column_names

data['datetime'] = pd.to_datetime(data['datetime'])
# data.set_index('datetime', inplace=True)
data

datetime      open      high       low     close       volume
0    2021-02-01 01:30:00  32807.29  32931.55  32461.23  32853.73  2968.315197
1    2021-02-01 02:30:00  32853.73  32899.39  32515.00  32560.73  2336.553165
2    2021-02-01 03:30:00  32561.35  33088.88  32559.85  32974.10  1874.807965
3    2021-02-01 04:30:00  32974.10  33255.49  32933.54  33092.98  3218.738903
4    2021-02-01 05:30:00  33092.97  33106.33  32296.16  32546.27  4383.926122
...                  ...       ...       ...       ...       ...          ...
8723 2022-01-31 01:30:00  37512.37  37740.00  37351.63  37684.45  1037.922560
8724 2022-01-31 02:30:00  37684.45  37762.60  37492.25  37729.00   874.060520
8725 2022-01-31 03:30:00  37729.00  37855.54  37625.41  37785.78   734.658550
8726 2022-01-31 04:30:00  37785.78  38230.00  37778.46  37881.76  1728.811800
8727 2022-01-31 05:30:00  37881.75  37951.07  36828.32  36829.30  2907.710960

[8728 rows x 6 columns]

In [332]:
nan_values = data.isna().sum()
nan_values

datetime    0
open        0
high        0
low         0
close       0
volume      0
dtype: int64

In [333]:
# rsi=vbt.RSI.run(data["close"],window=14)
# data['RSI']=rsi.rsi

In [334]:
# data.tail()

In [335]:
# from joblib import load

# loaded_clf = load('saved_rf_model.joblib')


In [336]:
# window_size_param=20
# threshold_param=100

In [337]:
# from sklearn.preprocessing import StandardScaler
# from ta.volatility import AverageTrueRange

# data['MA'] = data['close'].rolling(window=window_size_param).mean()

# data['price_diff'] = data['close'].diff()
# data['target'] = (data['price_diff'] > threshold_param).astype(int)

# data['ATR'] = AverageTrueRange(data['high'], data['low'], data['close'], window=14).average_true_range()

# for lag in range(1, 5):
#     data[f'lag_{lag}_ATR'] = data['ATR'].shift(lag)

# data.dropna(inplace=True)


# X_new = data[['MA', 'ATR', 'lag_1_ATR', 'lag_2_ATR', 'lag_3_ATR', 'lag_4_ATR']]

# scaler = StandardScaler()
# X_new_scaled = scaler.fit_transform(X_new)


# predictions = loaded_clf.predict(X_new_scaled)  

# data['predictions'] = predictions

In [338]:
def calculate_rsi(data, column, window=14):
    close_prices = data[column]
    daily_returns = close_prices.diff(1)
    gains = daily_returns.where(daily_returns > 0, 0)
    losses = -daily_returns.where(daily_returns < 0, 0)

    avg_gain = gains.rolling(window=window, min_periods=1).mean()
    avg_loss = losses.rolling(window=window, min_periods=1).mean()

    rs = avg_gain / avg_loss
    rsi = 100 - (100 / (1 + rs))

    return rsi

# Calculate Moving Average Convergence Divergence (MACD)
def calculate_macd(data, column, slow=26, fast=12, signal=9):
    exp12 = data[column].ewm(span=fast, adjust=False).mean()
    exp26 = data[column].ewm(span=slow, adjust=False).mean()

    macd = exp12 - exp26
    signal_line = macd.ewm(span=signal, adjust=False).mean()
    macd_hist = macd - signal_line

    return macd, signal_line, macd_hist

# Calculate Stochastic Oscillator (KD)
def calculate_stochastic_oscillator(data, high, low, close, window=14, smooth_window=3):
    high_max = high.rolling(window=window, min_periods=1).max()
    low_min = low.rolling(window=window, min_periods=1).min()

    k = ((close - low_min) / (high_max - low_min)) * 100
    d = k.rolling(window=smooth_window, min_periods=1).mean()

    return k, d

# Calculate Momentum (MOM)
def calculate_momentum(data, column, window=15):
    return data[column].diff(window)

In [339]:
# Feature Engineering - Manual Calculation of Technical Indicators
data["rsi"] = calculate_rsi(data, "close", window=14)
data["macd"], data["macdsig"], data["macdhist"] = calculate_macd(data, "close", slow=26, fast=12, signal=9)
data["kdf"], data["kds"] = calculate_stochastic_oscillator(data, data["high"], data["low"], data["close"], window=14, smooth_window=3)
data["mom"] = calculate_momentum(data, "close", window=15)


In [340]:
# Define the trend based on your criteria
data["short_mom"] = data["rsi"].rolling(window=10, min_periods=1, center=False).mean()
data["long_mom"] = data["rsi"].rolling(window=20, min_periods=1, center=False).mean()
data["short_mov"] = data["close"].rolling(window=10, min_periods=1, center=False).mean()
data["long_mov"] = data["close"].rolling(window=20, min_periods=1, center=False).mean()

In [341]:
data

datetime      open      high       low     close       volume  \
0    2021-02-01 01:30:00  32807.29  32931.55  32461.23  32853.73  2968.315197   
1    2021-02-01 02:30:00  32853.73  32899.39  32515.00  32560.73  2336.553165   
2    2021-02-01 03:30:00  32561.35  33088.88  32559.85  32974.10  1874.807965   
3    2021-02-01 04:30:00  32974.10  33255.49  32933.54  33092.98  3218.738903   
4    2021-02-01 05:30:00  33092.97  33106.33  32296.16  32546.27  4383.926122   
...                  ...       ...       ...       ...       ...          ...   
8723 2022-01-31 01:30:00  37512.37  37740.00  37351.63  37684.45  1037.922560   
8724 2022-01-31 02:30:00  37684.45  37762.60  37492.25  37729.00   874.060520   
8725 2022-01-31 03:30:00  37729.00  37855.54  37625.41  37785.78   734.658550   
8726 2022-01-31 04:30:00  37785.78  38230.00  37778.46  37881.76  1728.811800   
8727 2022-01-31 05:30:00  37881.75  37951.07  36828.32  36829.30  2907.710960   

            rsi        macd    macdsig   macdhist        kdf        kds  \
0           NaN    0.000000   0.000000   0.000000  83.453819  83.453819   
1      0.000000  -23.373219  -4.674644 -18.698575  21.155809  52.304814   
2     58.520322   -8.443825  -5.428480  -3.015345  81.712738  62.107455   
3     64.495607   12.832525  -1.776279  14.608804  79.539446  60.802664   
4     38.794863  -14.256403  -4.272304  -9.984099  26.071321  62.441168   
...         ...         ...        ...        ...        ...        ...   
8723  40.961362  -26.925338  35.148781 -62.074119  33.029981  19.158480   
8724  38.211991  -34.680651  21.182895 -55.863546  37.451247  26.033540   
8725  44.645517  -35.832072   9.779901 -45.611973  47.839693  39.440307   
8726  49.805624  -28.669315   2.090058 -30.759373  58.415885  47.902275   
8727  25.293105 -106.687675 -19.665489 -87.022187   0.068492  35.441357   

          mom  short_mom   long_mom     short_mov      long_mov  
0         NaN        NaN        NaN  32853.730000  32853.730000  
1         NaN   0.000000   0.000000  32707.230000  32707.230000  
2         NaN  29.260161  29.260161  32796.186667  32796.186667  
3         NaN  41.005310  41.005310  32870.385000  32870.385000  
4         NaN  40.452698  40.452698  32805.562000  32805.562000  
...       ...        ...        ...           ...           ...  
8723  -454.94  45.235850  50.693304  37867.200000  37956.456000  
8724  -369.51  44.710243  49.914299  37829.098000  37946.318500  
8725  -459.20  44.718328  49.541869  37813.829000  37938.017500  
8726  -118.24  45.248679  49.808902  37805.683000  37936.249000  
8727 -1060.18  42.708663  47.925771  37704.714000  37872.747000  

[8728 rows x 17 columns]

In [342]:
# Mark Labels
data['label'] = np.where(data.short_mov > data.long_mov, 1, 0)
data = data.drop(columns=["short_mov", "long_mov", "short_mom", "long_mom"])

In [343]:
data.set_index(data["datetime"], inplace=True)
data = data.fillna(method="pad", axis=0)
data = data.dropna(axis=0)

In [344]:
data.shape

(8713, 14)

In [345]:
from sklearn.preprocessing import StandardScaler
X = data.drop('label', axis=1)
X = X.drop('datetime', axis=1)
X[X.columns] = StandardScaler().fit_transform(X[X.columns])

In [346]:
X.shape

(8713, 12)

In [347]:
from tensorflow.keras.models import load_model

In [348]:
# data['Price Change'] = data['close'].diff()
# data['Gain'] = data['Price Change'].apply(lambda x: x if x > 0 else 0).rolling(window=14).mean()
# data['Loss'] = -data['Price Change'].apply(lambda x: x if x < 0 else 0).rolling(window=14).mean()
# data['RS'] = data['Gain'] / data['Loss']
# data['rsi'] = 100 - (100 / (1 + data['RS']))
# data = data.drop(['Price Change', 'Gain', 'Loss', 'RS'], axis=1)

# data["short_mom"] = data["rsi"].rolling(window=10, min_periods=1, center=False).mean()
# data["long_mom"] = data["rsi"].rolling(window=20, min_periods=1, center=False).mean()
# data["short_mov"] = data["close"].rolling(window=10, min_periods=1, center=False).mean()
# data["long_mov"] = data["close"].rolling(window=20, min_periods=1, center=False).mean()
# data.tail()

In [349]:
# data['label']=np.where(data.short_mov>data.long_mov,1,0)
# data['stoch_oscillator'] = ta.momentum.StochasticOscillator(data['high'], data['low'], data['close'], window=14, smooth_window=3).stoch()

# data['rsi'] = ta.momentum.RSIIndicator(data['close'], window=14).rsi()

# data['macd'] = ta.trend.MACD(data['close'], window_slow=26, window_fast=12, window_sign=9).macd()
# data.tail()

In [350]:
# data.dropna(inplace=True)
# data

In [351]:
X

open      high       low     close    volume  \
datetime                                                                
2021-02-01 16:30:00 -1.492367 -1.495272 -1.487205 -1.490295  0.839958   
2021-02-01 17:30:00 -1.490200 -1.488795 -1.524633 -1.534962  1.364316   
2021-02-01 18:30:00 -1.534865 -1.533053 -1.517591 -1.542313  0.961446   
2021-02-01 19:30:00 -1.542215 -1.552863 -1.545218 -1.560634  0.651643   
2021-02-01 20:30:00 -1.560243 -1.577421 -1.571220 -1.600926  0.021686   
...                       ...       ...       ...       ...       ...   
2022-01-31 01:30:00 -1.130255 -1.134729 -1.117097 -1.111729 -0.721760   
2022-01-31 02:30:00 -1.111650 -1.132289 -1.101862 -1.106912 -0.794132   
2022-01-31 03:30:00 -1.106833 -1.122257 -1.087435 -1.100772 -0.855702   
2022-01-31 04:30:00 -1.100694 -1.081835 -1.070854 -1.090394 -0.416615   
2022-01-31 05:30:00 -1.090317 -1.111945 -1.173792 -1.204194  0.104068   

                          rsi      macd   macdsig  macdhist       kdf  \
datetime                                                                
2021-02-01 16:30:00  1.159772  0.816044  0.614706  0.779768  0.903289   
2021-02-01 17:30:00  0.543587  0.746193  0.650492  0.441123  0.279390   
2021-02-01 18:30:00  0.410108  0.670284  0.662968  0.154349  0.176721   
2021-02-01 19:30:00  0.773756  0.571720  0.651975 -0.134377 -0.223015   
2021-02-01 20:30:00 -0.313314  0.418933  0.610670 -0.507308 -1.946478   
...                       ...       ...       ...       ...       ...   
2022-01-31 01:30:00 -0.589210 -0.071282  0.077066 -0.470288 -0.739113   
2022-01-31 02:30:00 -0.753209 -0.089270  0.042601 -0.423149 -0.577447   
2022-01-31 03:30:00 -0.369451 -0.091940  0.014461 -0.345339 -0.197586   
2022-01-31 04:30:00 -0.061651 -0.075327 -0.004516 -0.232606  0.189139   
2022-01-31 05:30:00 -1.523818 -0.256287 -0.058204 -0.659646 -1.944373   

                          kds       mom  
datetime                                 
2021-02-01 16:30:00  1.058108  0.882867  
2021-02-01 17:30:00  0.740250  0.802671  
2021-02-01 18:30:00  0.489426  0.481253  
2021-02-01 19:30:00  0.083695  0.288729  
2021-02-01 20:30:00 -0.718133  0.404963  
...                       ...       ...  
2022-01-31 01:30:00 -1.347181 -0.308747  
2022-01-31 02:30:00 -1.075503 -0.251701  
2022-01-31 03:30:00 -0.545717 -0.311591  
2022-01-31 04:30:00 -0.211331 -0.083918  
2022-01-31 05:30:00 -0.703741 -0.712891  

[8713 rows x 12 columns]

In [352]:
X = np.array(X)

In [353]:
X = np.reshape(X, (X.shape[0], 1, X.shape[1]))

In [354]:
# scaler = StandardScaler()
# # data = data.drop(['datetime', 'short_mom', 'long_mom', 'short_mov', 'long_mov','label'], axis=1)
# numeric_columns = ['open', 'high', 'low', 'close', 'volume', 'rsi','stoch_oscillator','macd'] 
# data[numeric_columns] = scaler.fit_transform(data[numeric_columns])
# data.dropna(inplace=True)
model = load_model('regressor.h5')
predictions=model.predict(X)
# X_test = data.values.reshape((data.shape[0], 1, data.shape[1]))
# X_test
# predictions = model.predict(X_test)
# predictions=predictions.astype(np.float64)
# print(predictions)

273/273 [==============================] - 1s 1ms/step


In [355]:
predictions

array([[9.9967664e-01],
       [9.9960417e-01],
       [9.9953699e-01],
       ...,
       [1.0862362e-03],
       [3.8038418e-03],
       [7.2728732e-04]], dtype=float32)

In [356]:
import numpy as np

threshold = 0.5
binary_predictions = (predictions >= threshold).astype(int)

count_0 = np.sum(binary_predictions == 0)
count_1 = np.sum(binary_predictions == 1)

print(f"Number of 0s: {count_0}, Number of 1s: {count_1}")


Number of 0s: 5551, Number of 1s: 3162


In [357]:
data

datetime      open      high       low  \
datetime                                                                
2021-02-01 16:30:00 2021-02-01 16:30:00  34163.28  34400.00  33935.47   
2021-02-01 17:30:00 2021-02-01 17:30:00  34183.33  34460.00  33590.00   
2021-02-01 18:30:00 2021-02-01 18:30:00  33770.23  34050.00  33655.00   
2021-02-01 19:30:00 2021-02-01 19:30:00  33702.25  33866.49  33400.00   
2021-02-01 20:30:00 2021-02-01 20:30:00  33535.51  33638.99  33160.00   
...                                 ...       ...       ...       ...   
2022-01-31 01:30:00 2022-01-31 01:30:00  37512.37  37740.00  37351.63   
2022-01-31 02:30:00 2022-01-31 02:30:00  37684.45  37762.60  37492.25   
2022-01-31 03:30:00 2022-01-31 03:30:00  37729.00  37855.54  37625.41   
2022-01-31 04:30:00 2022-01-31 04:30:00  37785.78  38230.00  37778.46   
2022-01-31 05:30:00 2022-01-31 05:30:00  37881.75  37951.07  36828.32   

                        close       volume        rsi        macd     macdsig  \
datetime                                                                        
2021-02-01 16:30:00  34183.33  4573.868890  70.282196  355.632270  253.010760   
2021-02-01 17:30:00  33770.23  5761.088940  59.952147  325.516853  267.511978   
2021-02-01 18:30:00  33702.25  4848.934356  57.714446  292.789653  272.567513   
2021-02-01 19:30:00  33532.81  4147.496698  63.810820  250.295469  268.113104   
2021-02-01 20:30:00  33160.17  2721.186603  45.586621  184.423667  251.375217   
...                       ...          ...        ...         ...         ...   
2022-01-31 01:30:00  37684.45  1037.922560  40.961362  -26.925338   35.148781   
2022-01-31 02:30:00  37729.00   874.060520  38.211991  -34.680651   21.182895   
2022-01-31 03:30:00  37785.78   734.658550  44.645517  -35.832072    9.779901   
2022-01-31 04:30:00  37881.76  1728.811800  49.805624  -28.669315    2.090058   
2022-01-31 05:30:00  36829.30  2907.710960  25.293105 -106.687675  -19.665489   

                       macdhist        kdf        kds      mom  label  
datetime                                                               
2021-02-01 16:30:00  102.621510  77.946479  80.026654  1329.60      1  
2021-02-01 17:30:00   58.004874  60.884057  71.982961  1209.50      1  
2021-02-01 18:30:00   20.222140  58.076254  65.635597   728.15      1  
2021-02-01 19:30:00  -17.817636  47.144266  55.368193   439.83      1  
2021-02-01 20:30:00  -66.951550   0.010917  35.077146   613.90      1  
...                         ...        ...        ...      ...    ...  
2022-01-31 01:30:00  -62.074119  33.029981  19.158480  -454.94      0  
2022-01-31 02:30:00  -55.863546  37.451247  26.033540  -369.51      0  
2022-01-31 03:30:00  -45.611973  47.839693  39.440307  -459.20      0  
2022-01-31 04:30:00  -30.759373  58.415885  47.902275  -118.24      0  
2022-01-31 05:30:00  -87.022187   0.068492  35.441357 -1060.18      0  

[8713 rows x 14 columns]

In [358]:
# original_columns = ['open', 'high', 'low', 'close', 'volume', 'rsi','stoch_oscillator','macd','macdsig',	'macdhist'	,'kdf'	,'kds'	,'mom'	,'short_mom'	,'long_mom',	'short_mov'	,'long_mov']
# scaler = StandardScaler()

# scaled_data = data[original_columns]

# unscaled_data = pd.DataFrame(scaler.inverse_transform(scaled_data), columns=original_columns)

# data[original_columns] = unscaled_data
# data

In [359]:
# print(type(predictions))


In [360]:
# model = load_model('your_model_name.h5')
# X = data.drop('label', axis=1)
# X = np.array(X)  
# X = np.reshape(X, (X.shape[0], 1, X.shape[1]))  

# predictions = model.predict(X)

In [361]:
# data['entry_long'] = (
#     (data['RSI'] > 50) & (data['RSI'].shift(1) <= 50)  # RSI crossed above 50
# ).astype(int)

# data['exit_long'] = (
#     (data['RSI'] < 50) & (data['RSI'].shift(1) >= 50)  # RSI crossed below 50
# ).astype(int)


In [363]:
predictions_reshaped = binary_predictions[:len(data)].reshape(-1)
data['entry_long'] = (
    (
        ((data['rsi'] > 20) & (data['rsi'].shift(1) <= 20) & (predictions_reshaped == 1)) |
        ((data['rsi'] > 50) & (data['rsi'].shift(1) <= 50) & (predictions_reshaped == 1))
    ) |
    ((data['rsi'] > 70) & (data['rsi'].shift(1) <= 70) & (predictions_reshaped == 1))
).astype(int)

data['exit_long'] = (
    ((data['rsi'] < 80) & (data['rsi'].shift(1) >= 80)) |
    ((data['rsi'] < 50) & (data['rsi'].shift(1) >= 50)) |
    ((data['rsi'] < 20) & (data['rsi'].shift(1) >= 20))
).astype(int)
# Assuming 'predictions' is the array you received from model.predict()
# 'data' is your DataFrame

# print(predictions_reshaped)


In [364]:
# data['entry_long'] = (
#     (
#         (predictions_reshaped == 1)
#     )
# ).astype(int)

# data['exit_long'] = (
#     (predictions_reshaped == 0)
# ).astype(int)


In [365]:
# data['entry_long'] = (
#     (data['rsi'] < 30)
# ).astype(int)

# data['exit_long'] = (
#     (data['rsi'] > 70)
# ).astype(int)

# Adjust RSI thresholds for entry and exit signals
# data['entry_long'] = (
#     ((data['rsi'] > 35) & (data['rsi'].shift(1) <= 35)) |  # Tweak threshold values
#     ((data['rsi'] > 65) & (data['rsi'].shift(1) <= 65))    # Tweak threshold values
# ).astype(int)

# data['exit_long'] = (
#     ((data['rsi'] < 75) & (data['rsi'].shift(1) >= 75)) |  # Tweak threshold values
#     ((data['rsi'] < 45) & (data['rsi'].shift(1) >= 45))    # Tweak threshold values
# ).astype(int)


In [366]:
# print(predictions[:, 0])

In [367]:

# price_increase_prob = loaded_clf.predict_proba(X_new_scaled)[:, 1]  

# data['entry_long'] = (
#     ((data['RSI'] > 20) & (data['RSI'].shift(1) <= 20) & (price_increase_prob >= 0.60)) |
#     ((data['RSI'] > 50) & (data['RSI'].shift(1) <= 50) & (price_increase_prob >= 0.60)) |
#     ((data['RSI'] > 70) & (data['RSI'].shift(1) <= 70) & (price_increase_prob >= 0.60))
# ).astype(int)

# data['exit_long'] = (
#     ((data['RSI'] < 80) & (data['RSI'].shift(1) >= 80)) |
#     ((data['RSI'] < 50) & (data['RSI'].shift(1) >= 50)) |
#     ((data['RSI'] < 20) & (data['RSI'].shift(1) >= 20))
# ).astype(int)


In [368]:
#mean reversion

In [369]:
# data['entry_long'] = (
#     (data['RSI'] > 20) & (data['RSI'].shift(1) <= 20) |  # RSI crossed above 20
#     (data['RSI'] > 50) & (data['RSI'].shift(1) <= 50) |  # RSI crossed above 50
#     (data['RSI'] > 70) & (data['RSI'].shift(1) <= 70)    # RSI crossed above 70
# ).astype(int)

# data['exit_long'] = (
#     (data['RSI'] < 80) & (data['RSI'].shift(1) >= 80) |  # RSI crossed below 80
#     (data['RSI'] < 50) & (data['RSI'].shift(1) >= 50) |  # RSI crossed below 50
#     (data['RSI'] < 20) & (data['RSI'].shift(1) >= 20)    # RSI crossed below 20
# ).astype(int)


In [370]:
data

datetime      open      high       low  \
datetime                                                                
2021-02-01 16:30:00 2021-02-01 16:30:00  34163.28  34400.00  33935.47   
2021-02-01 17:30:00 2021-02-01 17:30:00  34183.33  34460.00  33590.00   
2021-02-01 18:30:00 2021-02-01 18:30:00  33770.23  34050.00  33655.00   
2021-02-01 19:30:00 2021-02-01 19:30:00  33702.25  33866.49  33400.00   
2021-02-01 20:30:00 2021-02-01 20:30:00  33535.51  33638.99  33160.00   
...                                 ...       ...       ...       ...   
2022-01-31 01:30:00 2022-01-31 01:30:00  37512.37  37740.00  37351.63   
2022-01-31 02:30:00 2022-01-31 02:30:00  37684.45  37762.60  37492.25   
2022-01-31 03:30:00 2022-01-31 03:30:00  37729.00  37855.54  37625.41   
2022-01-31 04:30:00 2022-01-31 04:30:00  37785.78  38230.00  37778.46   
2022-01-31 05:30:00 2022-01-31 05:30:00  37881.75  37951.07  36828.32   

                        close       volume        rsi        macd     macdsig  \
datetime                                                                        
2021-02-01 16:30:00  34183.33  4573.868890  70.282196  355.632270  253.010760   
2021-02-01 17:30:00  33770.23  5761.088940  59.952147  325.516853  267.511978   
2021-02-01 18:30:00  33702.25  4848.934356  57.714446  292.789653  272.567513   
2021-02-01 19:30:00  33532.81  4147.496698  63.810820  250.295469  268.113104   
2021-02-01 20:30:00  33160.17  2721.186603  45.586621  184.423667  251.375217   
...                       ...          ...        ...         ...         ...   
2022-01-31 01:30:00  37684.45  1037.922560  40.961362  -26.925338   35.148781   
2022-01-31 02:30:00  37729.00   874.060520  38.211991  -34.680651   21.182895   
2022-01-31 03:30:00  37785.78   734.658550  44.645517  -35.832072    9.779901   
2022-01-31 04:30:00  37881.76  1728.811800  49.805624  -28.669315    2.090058   
2022-01-31 05:30:00  36829.30  2907.710960  25.293105 -106.687675  -19.665489   

                       macdhist        kdf        kds      mom  label  \
datetime                                                                
2021-02-01 16:30:00  102.621510  77.946479  80.026654  1329.60      1   
2021-02-01 17:30:00   58.004874  60.884057  71.982961  1209.50      1   
2021-02-01 18:30:00   20.222140  58.076254  65.635597   728.15      1   
2021-02-01 19:30:00  -17.817636  47.144266  55.368193   439.83      1   
2021-02-01 20:30:00  -66.951550   0.010917  35.077146   613.90      1   
...                         ...        ...        ...      ...    ...   
2022-01-31 01:30:00  -62.074119  33.029981  19.158480  -454.94      0   
2022-01-31 02:30:00  -55.863546  37.451247  26.033540  -369.51      0   
2022-01-31 03:30:00  -45.611973  47.839693  39.440307  -459.20      0   
2022-01-31 04:30:00  -30.759373  58.415885  47.902275  -118.24      0   
2022-01-31 05:30:00  -87.022187   0.068492  35.441357 -1060.18      0   

                     entry_long  exit_long  
datetime                                    
2021-02-01 16:30:00           0          0  
2021-02-01 17:30:00           0          0  
2021-02-01 18:30:00           0          0  
2021-02-01 19:30:00           0          0  
2021-02-01 20:30:00           0          1  
...                         ...        ...  
2022-01-31 01:30:00           0          0  
2022-01-31 02:30:00           0          0  
2022-01-31 03:30:00           0          0  
2022-01-31 04:30:00           0          0  
2022-01-31 05:30:00           0          0  

[8713 rows x 16 columns]

In [371]:
num_entry_long = data['entry_long'].sum()
num_exit_long = data['exit_long'].sum()
print(num_entry_long)
print(num_exit_long)

345
798


In [372]:
data.dropna(inplace=True)
data

datetime      open      high       low  \
datetime                                                                
2021-02-01 16:30:00 2021-02-01 16:30:00  34163.28  34400.00  33935.47   
2021-02-01 17:30:00 2021-02-01 17:30:00  34183.33  34460.00  33590.00   
2021-02-01 18:30:00 2021-02-01 18:30:00  33770.23  34050.00  33655.00   
2021-02-01 19:30:00 2021-02-01 19:30:00  33702.25  33866.49  33400.00   
2021-02-01 20:30:00 2021-02-01 20:30:00  33535.51  33638.99  33160.00   
...                                 ...       ...       ...       ...   
2022-01-31 01:30:00 2022-01-31 01:30:00  37512.37  37740.00  37351.63   
2022-01-31 02:30:00 2022-01-31 02:30:00  37684.45  37762.60  37492.25   
2022-01-31 03:30:00 2022-01-31 03:30:00  37729.00  37855.54  37625.41   
2022-01-31 04:30:00 2022-01-31 04:30:00  37785.78  38230.00  37778.46   
2022-01-31 05:30:00 2022-01-31 05:30:00  37881.75  37951.07  36828.32   

                        close       volume        rsi        macd     macdsig  \
datetime                                                                        
2021-02-01 16:30:00  34183.33  4573.868890  70.282196  355.632270  253.010760   
2021-02-01 17:30:00  33770.23  5761.088940  59.952147  325.516853  267.511978   
2021-02-01 18:30:00  33702.25  4848.934356  57.714446  292.789653  272.567513   
2021-02-01 19:30:00  33532.81  4147.496698  63.810820  250.295469  268.113104   
2021-02-01 20:30:00  33160.17  2721.186603  45.586621  184.423667  251.375217   
...                       ...          ...        ...         ...         ...   
2022-01-31 01:30:00  37684.45  1037.922560  40.961362  -26.925338   35.148781   
2022-01-31 02:30:00  37729.00   874.060520  38.211991  -34.680651   21.182895   
2022-01-31 03:30:00  37785.78   734.658550  44.645517  -35.832072    9.779901   
2022-01-31 04:30:00  37881.76  1728.811800  49.805624  -28.669315    2.090058   
2022-01-31 05:30:00  36829.30  2907.710960  25.293105 -106.687675  -19.665489   

                       macdhist        kdf        kds      mom  label  \
datetime                                                                
2021-02-01 16:30:00  102.621510  77.946479  80.026654  1329.60      1   
2021-02-01 17:30:00   58.004874  60.884057  71.982961  1209.50      1   
2021-02-01 18:30:00   20.222140  58.076254  65.635597   728.15      1   
2021-02-01 19:30:00  -17.817636  47.144266  55.368193   439.83      1   
2021-02-01 20:30:00  -66.951550   0.010917  35.077146   613.90      1   
...                         ...        ...        ...      ...    ...   
2022-01-31 01:30:00  -62.074119  33.029981  19.158480  -454.94      0   
2022-01-31 02:30:00  -55.863546  37.451247  26.033540  -369.51      0   
2022-01-31 03:30:00  -45.611973  47.839693  39.440307  -459.20      0   
2022-01-31 04:30:00  -30.759373  58.415885  47.902275  -118.24      0   
2022-01-31 05:30:00  -87.022187   0.068492  35.441357 -1060.18      0   

                     entry_long  exit_long  
datetime                                    
2021-02-01 16:30:00           0          0  
2021-02-01 17:30:00           0          0  
2021-02-01 18:30:00           0          0  
2021-02-01 19:30:00           0          0  
2021-02-01 20:30:00           0          1  
...                         ...        ...  
2022-01-31 01:30:00           0          0  
2022-01-31 02:30:00           0          0  
2022-01-31 03:30:00           0          0  
2022-01-31 04:30:00           0          0  
2022-01-31 05:30:00           0          0  

[8713 rows x 16 columns]

In [373]:
# data2 = pd.read_csv('btc_1h_test.csv')
# column_names = ['datetime', 'open', 'high', 'low', 'close', 'volume']
# data2.columns = column_names

# data2['datetime'] = pd.to_datetime(data2['datetime'])
# rsi=vbt.RSI.run(data["close"],window=14)
# data2['RSI']=rsi.rsi
# data2.dropna(inplace=True)
# data2

In [374]:
fees = 0.0015 
stop_loss = 0.01
# take_profit = 0.0
sl_trail = 0.01

In [375]:
# position_sizes = {
#     35: 0.03,  
#     65: 0.07   
# }

# data['position_size'] = 0.0  

# for threshold, size in position_sizes.items():
#     condition = (data['rsi'] > threshold) & (data['rsi'].shift(1) <= threshold)
#     data.loc[condition, 'position_size'] = size
position_sizes = {
    20: 0.02,  # Adjusted for entry condition (RSI < 20)
    50: 0.05,  # Adjusted for entry condition (RSI < 50)
    70: 0.07   # Adjusted for entry condition (RSI > 70)
}

data['position_size'] = 0.0

for threshold, size in position_sizes.items():
    if threshold in [20, 50, 70]:  # Adjust for respective entry conditions
        condition_entry = (data['rsi'] < threshold)
        data.loc[condition_entry, 'position_size'] = size


portfolio = vbt.Portfolio.from_signals(
    close=data['close'], 
    entries=data['entry_long'],  
    exits=data['exit_long'],
    size=data['position_size'],  
    size_type="Percent",
    fees=fees,  
    sl_stop=stop_loss,
    tp_stop= 0.03,
    sl_trail=sl_trail ,
    init_cash=100000
)

portfolio_stats = portfolio.stats()
portfolio_stats


/home/outbreakkp/anaconda3/envs/vectorbt_env/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sharpe_ratio' requires frequency to be set

/home/outbreakkp/anaconda3/envs/vectorbt_env/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'calmar_ratio' requires frequency to be set

/home/outbreakkp/anaconda3/envs/vectorbt_env/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'omega_ratio' requires frequency to be set

/home/outbreakkp/anaconda3/envs/vectorbt_env/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:396: UserWarning:

Metric 'sortino_ratio' requires frequency to be set



Start                         2021-02-01 16:30:00
End                           2022-01-31 05:30:00
Period                                       8713
Start Value                              100000.0
End Value                            95501.927443
Total Return [%]                        -4.498073
Benchmark Return [%]                     7.740527
Max Gross Exposure [%]                   7.184022
Total Fees Paid                       3326.811518
Max Drawdown [%]                         4.815722
Max Drawdown Duration                      8614.0
Total Trades                                  163
Total Closed Trades                           163
Total Open Trades                               0
Open Trade PnL                                0.0
Win Rate [%]                            22.699387
Best Trade [%]                            5.78113
Worst Trade [%]                         -8.253506
Avg Winning Trade [%]                    1.722139
Avg Losing Trade [%]                    -1.027058


In [295]:
# portfolio = vbt.Portfolio.from_signals(
#     close=data['close'], 
#     entries=data['entry_long'],  
#     exits=data['exit_long'],
#     slippage=slippage,  
#     sl_stop=stop_loss,  
#     tp_stop=take_profit,
#     sl_trail=sl_trail 
# )

# portfolio_stats = portfolio.stats()
# portfolio_stats

In [296]:
!pip install nbformat --upgrade

In [297]:
portfolio.plots().show()

In [ ]:
import matplotlib.pyplot as plt

plt.figure(figsize=(10, 6))
plt.plot(data.index, data['RSI'], label='RSI', color='blue')
plt.axhline(y=20, color='orange', linestyle='--', label='RSI 20')
plt.axhline(y=50, color='green', linestyle='--', label='RSI 50')
plt.axhline(y=70, color='red', linestyle='--', label='RSI 70')
plt.axhline(y=80, color='purple', linestyle='--', label='RSI 80')
plt.axhline(y=50, color='gray', linestyle='--')
plt.xlabel('Date')
plt.ylabel('RSI')
plt.title('RSI Over Time')
plt.legend()
plt.show()


KeyError: 'RSI'

<Figure size 1000x600 with 0 Axes>

In [ ]:
import seaborn as sns

plt.figure(figsize=(8, 6))
sns.histplot(data['RSI'], bins=50, kde=True, color='skyblue')
plt.axvline(x=20, color='orange', linestyle='--', label='RSI 20')
plt.axvline(x=50, color='green', linestyle='--', label='RSI 50')
plt.axvline(x=70, color='red', linestyle='--', label='RSI 70')
plt.axvline(x=80, color='purple', linestyle='--', label='RSI 80')
plt.xlabel('RSI')
plt.ylabel('Frequency')
plt.title('Distribution of RSI Values')
plt.legend()
plt.show()
